In [21]:
import pandas as pd

pd.core.common.is_list_like = pd.api.types.is_list_like
from pandas_datareader import data
import pandas
import  numpy as np
from datetime import datetime, timedelta

import fix_yahoo_finance as yf
yf.pdr_override() # <== that's all it takes :-)

pd.options.mode.chained_assignment = None


from bokeh.plotting import figure
from bokeh.io import push_notebook, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.io import output_notebook
from bokeh.models.tools import HoverTool

from bokeh.models import LinearAxis, Range1d
output_notebook()

from bokeh.palettes import Category20 as palettes
# itertools handles the cycling
import itertools 

colors = itertools.cycle(palettes[20]) 


%matplotlib notebook

Loading BokehJS ...

In [40]:
path= "~/Desktop/tmp/SPY.csv"

df=pd.read_csv(path, delimiter=",")

df.head()

Dates     Open    Close     High      Low
0  11/16/18 22:30  2718.54  2716.39  2718.54  2716.26
1  11/16/18 22:31  2716.53  2718.58  2719.99  2716.53
2  11/16/18 22:32  2718.73  2717.48  2719.59  2717.13
3  11/16/18 22:33  2717.27  2718.60  2719.70  2716.95
4  11/16/18 22:34  2718.39  2716.17  2718.60  2716.17

# convert timezone to ny time

In [41]:
df.Dates=pd.to_datetime(df.Dates)
df=df.set_index('Dates')


df= df.tz_localize(tz='Hongkong')
df = df.tz_convert('US/Eastern')

In [48]:
day=datetime.strptime('2018-01-01 04:59:59', '%Y-%m-%d %H:%M:%S')
df = df[day:]
resampled_df = df.resample('1min').interpolate(method='linear')
market = "EQ"
#HKG TIME
#futures 
if market =="FT":
    resampled_df = resampled_df[
                    
                        ( (resampled_df.index.weekday >0) & (resampled_df.index.weekday <= 5)  & (resampled_df.index.hour<=4))
                        | ((resampled_df.index.weekday<=4) & (resampled_df.index.hour>=6)) 
                        

                        #| ((resampled_df.index.weekday==6) & (resampled_df.index.hour>=22))
                       ]
elif market == "FX":
    resampled_df =resampled_df[ ((resampled_df.index.weekday <= 4)  & (resampled_df.index.hour<=4))
                        | ((resampled_df.index.weekday<=4) & (resampled_df.index.hour>=5)) 
                        | ((resampled_df.index.weekday==5) & (resampled_df.index.hour<=4))
                       ]
elif market == "EQ":
    print(" Equity")
    resampled_df =resampled_df[ 
        
                        ( (resampled_df.index.weekday >=0) & (resampled_df.index.weekday <= 4) 
                        &( (resampled_df.index.hour>=9 & resampled_df.index.hour<16) 
                          | (resampled_df.index.hour==9 & resampled_df.index.minute>=30)
                         | (resampled_df.index.hour==16 & resampled_df.index.minute==0)
                         )
                        )
                      
                        
                       ]
elif market =="CRYPTO":
    print("Crypto")


resampled_df['hour']=resampled_df.index.hour
resampled_df['minute']=resampled_df.index.minute
resampled_df['weekday']=resampled_df.index.weekday

 Equity


In [50]:
resampled_df.head()

Open    Close     High      Low  hour  minute  \
Dates                                                                         
2018-11-16 09:30:00-05:00  2718.54  2716.39  2718.54  2716.26     9      30   
2018-11-16 09:31:00-05:00  2716.53  2718.58  2719.99  2716.53     9      31   
2018-11-16 09:32:00-05:00  2718.73  2717.48  2719.59  2717.13     9      32   
2018-11-16 09:33:00-05:00  2717.27  2718.60  2719.70  2716.95     9      33   
2018-11-16 09:34:00-05:00  2718.39  2716.17  2718.60  2716.17     9      34   

                           weekday  
Dates                               
2018-11-16 09:30:00-05:00        4  
2018-11-16 09:31:00-05:00        4  
2018-11-16 09:32:00-05:00        4  
2018-11-16 09:33:00-05:00        4  
2018-11-16 09:34:00-05:00        4

In [6]:
plot_df = resampled_df


hover = HoverTool()

hover.tooltips = [
    ("x, y", "@x,@y"), 
]
colNameList=['Open','Close','High','Low']
p=figure( x_axis_type='datetime')
coloer=['red','yellow','green','blue','orange']
tf=[5,10,15,30,60]
for i in range(len(colNameList)):
    p.line(x=plot_df.index ,y=plot_df[colNameList[i]], 
           color=next(colors),legend=colNameList[i]
           )
    
p.tools.append(hover)
show(p)

In [53]:
plot_df = resampled_df['2019-01-15']
plot_df

Open        Close         High          Low  \
Dates                                                                           
2019-01-15 00:00:00-05:00  2583.730019  2583.995405  2584.292278  2583.730019   
2019-01-15 00:01:00-05:00  2583.732423  2583.998378  2584.295888  2583.732423   
2019-01-15 00:02:00-05:00  2583.734826  2584.001351  2584.299498  2583.734826   
2019-01-15 00:03:00-05:00  2583.737230  2584.004324  2584.303108  2583.737230   
2019-01-15 00:04:00-05:00  2583.739633  2584.007297  2584.306718  2583.739633   
2019-01-15 00:05:00-05:00  2583.742037  2584.010270  2584.310328  2583.742037   
2019-01-15 00:06:00-05:00  2583.744440  2584.013243  2584.313938  2583.744440   
2019-01-15 00:07:00-05:00  2583.746844  2584.016216  2584.317548  2583.746844   
2019-01-15 00:08:00-05:00  2583.749247  2584.019189  2584.321158  2583.749247   
2019-01-15 00:09:00-05:00  2583.751651  2584.022162  2584.324768  2583.751651   
2019-01-15 00:10:00-05:00  2583.754054  2584.025135  2584.328378  2583.754054   
2019-01-15 00:11:00-05:00  2583.756458  2584.028108  2584.331988  2583.756458   
2019-01-15 00:12:00-05:00  2583.758861  2584.031081  2584.335598  2583.758861   
2019-01-15 00:13:00-05:00  2583.761264  2584.034054  2584.339208  2583.761264   
2019-01-15 00:14:00-05:00  2583.763668  2584.037027  2584.342819  2583.763668   
2019-01-15 00:15:00-05:00  2583.766071  2584.040000  2584.346429  2583.766071   
2019-01-15 00:16:00-05:00  2583.768475  2584.042973  2584.350039  2583.768475   
2019-01-15 00:17:00-05:00  2583.770878  2584.045946  2584.353649  2583.770878   
2019-01-15 00:18:00-05:00  2583.773282  2584.048919  2584.357259  2583.773282   
2019-01-15 00:19:00-05:00  2583.775685  2584.051892  2584.360869  2583.775685   
2019-01-15 00:20:00-05:00  2583.778089  2584.054865  2584.364479  2583.778089   
2019-01-15 00:21:00-05:00  2583.780492  2584.057838  2584.368089  2583.780492   
2019-01-15 00:22:00-05:00  2583.782896  2584.060811  2584.371699  2583.782896   
2019-01-15 00:23:00-05:00  2583.785299  2584.063784  2584.375309  2583.785299   
2019-01-15 00:24:00-05:00  2583.787703  2584.066757  2584.378919  2583.787703   
2019-01-15 00:25:00-05:00  2583.790106  2584.069730  2584.382529  2583.790106   
2019-01-15 00:26:00-05:00  2583.792510  2584.072703  2584.386139  2583.792510   
2019-01-15 00:27:00-05:00  2583.794913  2584.075676  2584.389749  2583.794913   
2019-01-15 00:28:00-05:00  2583.797317  2584.078649  2584.393359  2583.797317   
2019-01-15 00:29:00-05:00  2583.799720  2584.081622  2584.396969  2583.799720   
...                                ...          ...          ...          ...   
2019-01-15 23:30:00-05:00  2612.172780  2612.248533  2612.412664  2611.878185   
2019-01-15 23:31:00-05:00  2612.177075  2612.253002  2612.417510  2611.881805   
2019-01-15 23:32:00-05:00  2612.181371  2612.257471  2612.422355  2611.885425   
2019-01-15 23:33:00-05:00  2612.185666  2612.261940  2612.427201  2611.889044   
2019-01-15 23:34:00-05:00  2612.189961  2612.266409  2612.432046  2611.892664   
2019-01-15 23:35:00-05:00  2612.194257  2612.270878  2612.436892  2611.896284   
2019-01-15 23:36:00-05:00  2612.198552  2612.275347  2612.441737  2611.899903   
2019-01-15 23:37:00-05:00  2612.202847  2612.279817  2612.446583  2611.903523   
2019-01-15 23:38:00-05:00  2612.207143  2612.284286  2612.451429  2611.907143   
2019-01-15 23:39:00-05:00  2612.211438  2612.288755  2612.456274  2611.910763   
2019-01-15 23:40:00-05:00  2612.215734  2612.293224  2612.461120  2611.914382   
2019-01-15 23:41:00-05:00  2612.220029  2612.297693  2612.465965  2611.918002   
2019-01-15 23:42:00-05:00  2612.224324  2612.302162  2612.470811  2611.921622   
2019-01-15 23:43:00-05:00  2612.228620  2612.306631  2612.475656  2611.925241   
2019-01-15 23:44:00-05:00  2612.232915  2612.311100  2612.480502  2611.928861   
2019-01-15 23:45:00-05:00  2612.237210  2612.315569  2612.485347  2611.932481   
2019-01-15 23:46:00-05:00  2612.241506  2612.320039  2612.490193 

Open    Close     High      Low  hour  minute  \
Dates                                                                         
2018-11-16 09:30:00-05:00  2718.54  2716.39  2718.54  2716.26    22      30   
2018-11-16 09:31:00-05:00  2716.53  2718.58  2719.99  2716.53    22      31   
2018-11-16 09:32:00-05:00  2718.73  2717.48  2719.59  2717.13    22      32   
2018-11-16 09:33:00-05:00  2717.27  2718.60  2719.70  2716.95    22      33   
2018-11-16 09:34:00-05:00  2718.39  2716.17  2718.60  2716.17    22      34   
2018-11-16 09:35:00-05:00  2716.14  2715.03  2716.68  2714.74    22      35   
2018-11-16 09:36:00-05:00  2714.89  2713.29  2715.46  2713.29    22      36   
2018-11-16 09:37:00-05:00  2713.17  2714.39  2714.77  2712.16    22      37   
2018-11-16 09:38:00-05:00  2714.40  2713.80  2714.61  2713.55    22      38   
2018-11-16 09:39:00-05:00  2713.93  2713.27  2715.04  2713.27    22      39   
2018-11-16 09:40:00-05:00  2713.28  2714.77  2715.81  2712.98    22      40   
2018-11-16 09:41:00-05:00  2714.81  2716.13  2716.64  2714.81    22      41   
2018-11-16 09:42:00-05:00  2717.66  2717.33  2719.13  2717.07    22      42   
2018-11-16 09:43:00-05:00  2717.17  2716.24  2717.44  2716.09    22      43   
2018-11-16 09:44:00-05:00  2716.21  2717.64  2717.64  2715.96    22      44   
2018-11-16 09:45:00-05:00  2717.74  2718.98  2721.26  2717.74    22      45   
2018-11-16 09:46:00-05:00  2719.62  2723.12  2723.14  2719.62    22      46   
2018-11-16 09:47:00-05:00  2723.04  2722.65  2723.18  2722.03    22      47   
2018-11-16 09:48:00-05:00  2722.74  2724.95  2724.96  2722.52    22      48   
2018-11-16 09:49:00-05:00  2724.84  2724.79  2725.54  2724.26    22      49   
2018-11-16 09:50:00-05:00  2724.72  2724.23  2724.77  2723.89    22      50   
2018-11-16 09:51:00-05:00  2724.23  2726.08  2726.66  2724.23    22      51   
2018-11-16 09:52:00-05:00  2726.10  2725.48  2726.63  2725.41    22      52   
2018-11-16 09:53:00-05:00  2725.48  2726.20  2726.71  2725.48    22      53   
2018-11-16 09:54:00-05:00  2726.21  2727.06  2727.64  2726.21    22      54   
2018-11-16 09:55:00-05:00  2727.02  2724.48  2727.02  2724.48    22      55   
2018-11-16 09:56:00-05:00  2724.43  2724.99  2725.37  2724.41    22      56   
2018-11-16 09:57:00-05:00  2725.09  2725.61  2725.61  2724.99    22      57   
2018-11-16 09:58:00-05:00  2725.60  2726.28  2726.85  2725.60    22      58   
2018-11-16 09:59:00-05:00  2726.27  2727.88  2728.48  2725.85    22      59   
...                            ...      ...      ...      ...   ...     ...   
2019-05-30 15:30:00-04:00  2785.68  2783.58  2785.68  2783.58     3      30   
2019-05-30 15:31:00-04:00  2783.56  2783.39  2783.75  2783.04     3      31   
2019-05-30 15:32:00-04:00  2783.36  2784.88  2784.94  2783.34     3      32   
2019-05-30 15:33:00-04:00  2784.87  2785.10  2785.10  2784.60     3      33   
2019-05-30 15:34:00-04:00  2785.09  2785.59  2785.59  2784.97     3      34   
2019-05-30 15:35:00-04:00  2785.55  2788.49  2788.49  2785.55     3      35   
2019-05-30 15:36:00-04:00  2788.50  2788.30  2788.50  2787.63     3      36   
2019-05-30 15:37:00-04:00  2788.47  2789.79  2789.79  2788.47     3      37   
2019-05-30 15:38:00-04:00  2789.79  2789.80  2791.10  2789.38     3      38   
2019-05-30 15:39:00-04:00  2789.79  2789.04  2789.86  2789.04     3      39   
2019-05-30 15:40:00-04:00  2789.00  2788.72  2789.43  2788.58     3      40   
2019-05-30 15:41:00-04:00  2788.72  2788.53  2789.42  2788.51     3      41   
2019-05-30 15:42:00-04:00  2788.52  2788.40  2789.02  2788.40     3      42   
2019-05-30 15:43:00-04:00  2788.39  2787.34  2788.39  2787.29     3      43   
2019-05-30 15:44:00-04:00  2787.34  2788.34  2788.37  2787.33     3      44   
2019-05-30 15:45:00-04:00  2788.25  2786.90  2788.25  2786.89     3      45   
2019-05-30 15:46:00-04:00  2786.89  2788.31  2788.54  2786.77     3      46   
2019-05-30 15:47:00-04:00  2788.32  2788.90  2788.99  2788.30     3      47   
2